## 用 Mobile site 就成功了!!!!

In [20]:
import urllib.request
from bs4 import BeautifulSoup
import gzip
import html5lib
import pandas as pd
import time

In [107]:
agents = {
    'accept': 'text/html,application/xhtml+xml,application/xml;q=0.9,image/webp,image/apng,*/*;q=0.8',
    'accept-Encoding': 'gzip, deflate',
    'accept-Language': 'zh-TW,zh;q=0.9,en-US;q=0.8,en;q=0.7,zh-CN;q=0.6',
    'cache-Control': 'max-age=0',
    'connection': 'keep-alive',
    'cookie': 'webauth=ug=7E36396631663D263E12395339&uc=1&un=e419d45f-3610-4919-8108-5ae3d1f24dd3&am=IP&pg=; VQPANKPS=025cef8b64-fab4-44Ds9EBfpGVK5C752Jx_JqeWZ7fLT-u4WXRGQ1xYADDrwsoQVESlHm0CKGvFahw5X5orw; BIGipServersdc-web-to-avi_80=593711882.20480.0000; __atuvc=9%7C43; EHost2=sid=a3a4fd39-3947-4105-aef7-4e23624f2a77@sessionmgr4007&k2=dGJyMPGstEqvq7dRrOPfgeyk44Dt6fIA&k3=dGJyMOPmtUq2qrBM&k4=ehost&k6=en&k7=live&k8=DS:live; amplitude_id_06d3064c4b7aa1187920f7d63c355898ebscohost.com=eyJkZXZpY2VJZCI6IjdjZDY5NjQxLTBmMGUtNDM2MC05MGJlLWNmNjIyNDA4YmViZVIiLCJ1c2VySWQiOm51bGwsIm9wdE91dCI6ZmFsc2UsInNlc3Npb25JZCI6MTU0MDIyMDc1NTQ3OCwibGFzdEV2ZW50VGltZSI6MTU0MDIyMDc3NTkyNiwiZXZlbnRJZCI6MzQsImlkZW50aWZ5SWQiOjM0LCJzZXF1ZW5jZU51bWJlciI6Njh9',
    'host': 'web.b.ebscohost.com',
    'upgrade-Insecure-Requests': '1',
    'user-Agent': 'Mozilla/5.0 (Windows NT 10.0) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/65.0.3325.181 Safari/537.36'
}
page = 1
news_count = 1
pre_url = "http://web.a.ebscohost.com/ehost/Results/GetMoreResults?sid=f1ce0be5-b13d-42fc-a8b5-2823e3525237@sdc-v-sessmgr06&vid=4&currentPage="
page1_url = "http://web.a.ebscohost.com/ehost/Results/ResultList?sid=f1ce0be5-b13d-42fc-a8b5-2823e3525237%40sdc-v-sessmgr06&vid=4"
first_soup = news_crawler(page1_url,agents)
total_page = int(int(first_soup.find("span",{"class":"total-count"}).get_text().replace(',',''))/10)

AttributeError: 'NoneType' object has no attribute 'get_text'

In [104]:
def get_titles_and_urls(url,agents):
    current_titles = list()
    current_urls = list()
    request = urllib.request.Request(url, headers=agents)
    html = urllib.request.urlopen(request, timeout=5).read()
    encoding = (urllib.request.urlopen(request, timeout=5)).getheader('Content-Encoding')
    html = gzip.decompress(html).decode("utf-8")
    soup = BeautifulSoup(html, "html5lib")
    titles = soup.findAll("h2",{"class":"record-title"})
    pre = "http://web.b.ebscohost.com"
    for title in titles:
        current_titles.append(title.a['title'])
        current_urls.append(pre+title.a['href'])
    return(current_titles,current_urls)

def news_crawler(url,agents):
    request = urllib.request.Request(url, headers=agents)
    html = urllib.request.urlopen(request, timeout=5).read()
    encoding = (urllib.request.urlopen(request, timeout=5)).getheader('Content-Encoding')
    #    print(encoding)
    html = gzip.decompress(html).decode("utf-8")
#     html = html[html.find(sub_start):html.find(sub_end)]
    soup = BeautifulSoup(html, "html5lib")
    return(soup)

def get_news_content(news_soup):
    article = str()
    body = news_soup.findAll("p",{"class":"body-paragraph"})
    for p in body:
        article = article+p.get_text()
    return(article)

def get_detail_info(detail_soup):
    info = dict()
    typical_features = ['Source ', 'Document Type ', 'Subjects ', 'Abstract ', 'Lexile ', 'Accession Number ', 'Database ']
    for typical_feature in typical_features:
        info[typical_feature] = ''
    info_types = detail_soup.findAll("dt")
    features = detail_soup.findAll("dd")
    num = 0
    title = detail_soup.head.title.get_text()
    info['title'] = title
    for info_type in info_types:
        text = features[num].get_text(strip=True).replace('\n','')
        info_type = info_type.get_text().replace(':','')
        if info_type in typical_features:
            info[info_type]=text
        num=num+1
    return(info)

def get_news_feature(detail_url):
    detail_soup = news_crawler(detail_url,agents)
    content = get_news_content(detail_soup)
    detail_info = get_detail_info(detail_soup)
    detail_info['content'] = content
    detail_info = pd.DataFrame.from_dict(detail_info,"index").T
    return(detail_info)

In [ ]:
page1_url = "http://web.b.ebscohost.com/ehost/Results/ResultList?sid=5171798b-1921-40bf-a5db-1b0a835edb7c%40pdc-v-sessmgr03&vid=4"
first_soup = news_crawler(page1_url,agents)
total_page = int(int(first_soup.find("span",{"class":"total-count"}).get_text().replace(',',''))/10)

In [110]:
pre_url = "http://web.b.ebscohost.com/ehost/Results/GetMoreResults?sid=f03ada46-abfb-4a02-92c2-c9ce10733fc4@sessionmgr120&vid=4&currentPage="


page = 317
news_count = 3160

while(page<total_page):
    if page == 1:
        current_titles, current_urls = get_titles_and_urls(page1_url,agents)
    else:
        try:
            current_titles, current_urls = get_titles_and_urls(pre_url+str(page),agents)
        except:
            print("wait")
            time.sleep(30)
            pass
    for i in range(0,len(current_urls)):
        try:
            detail_info = get_news_feature(current_urls[i])
            detail_info.to_csv("History_news_data.csv",header=False,mode='a',encoding = 'utf-8')
            print("---news:",news_count)
            news_count = news_count+1
        except:
            print("wait")
            time.sleep(10)
            pass
    print("Downloaded page:",page)
    print(detail_info)
    page = page + 1

---news: 3160
---news: 3161
---news: 3162
---news: 3163
---news: 3164
---news: 3165
---news: 3166
---news: 3167
---news: 3168
---news: 3169
Downloaded page: 317
                                   Source  Document Type  Subjects  Abstract   \
0  Savannah Morning News (GA). 10/11/2004.                                      

  Lexile  Accession Number          Database   \
0             2W62078292162  Newspaper Source   

                                               title  \
0  Analysts speculate that crude oil prices will ...   

                                             content  
0  Oct. 11--There's been no relief at the pump ov...  
---news: 3170
---news: 3171
---news: 3172
---news: 3173
---news: 3174
---news: 3175
---news: 3176
---news: 3177
---news: 3178
---news: 3179
Downloaded page: 318
                                   Source  Document Type  Subjects   \
0  International Business Times. 20120731.        Article             

                                           Abstrac

---news: 3280
---news: 3281
---news: 3282
---news: 3283
---news: 3284
---news: 3285
---news: 3286
---news: 3287
---news: 3288
---news: 3289
Downloaded page: 329
                                      Source  Document Type  Subjects   \
0  Dallas Morning News, The (TX). 02/27/2003.                            

  Abstract  Lexile  Accession Number          Database   \
0                       2W63295373098  Newspaper Source   

                               title  \
0  Crude Oil Prices Hit 12-Year High   

                                             content  
0  Feb. 27--Crude oil prices jumped Wednesday to ...  
---news: 3290
---news: 3291
---news: 3292
---news: 3293
---news: 3294
---news: 3295
---news: 3296
---news: 3297
---news: 3298
---news: 3299
Downloaded page: 330
                                       Source  Document Type   \
0  Investors Business Daily. 2/9/2016, p1. 1p.        Article   

                                           Subjects   \
0  PETROLEUM sales & pricesECONO

---news: 3400
---news: 3401
---news: 3402
---news: 3403
---news: 3404
---news: 3405
---news: 3406
---news: 3407
---news: 3408
---news: 3409
Downloaded page: 341
                                             Source  Document Type  Subjects   \
0  Journal Record, The (Oklahoma City, OK). 09/01...                            

  Abstract  Lexile  Accession Number                Database   \
0                       L54627034JROK  Regional Business News   

                                               title  \
0  Tulsa-based Magellan adding crude oil storage ...   

                                             content  
0  Magellan Midstream Partners LP is moving forwa...  
---news: 3410
---news: 3411
---news: 3412
---news: 3413
---news: 3414
---news: 3415
---news: 3416
---news: 3417
---news: 3418
---news: 3419
Downloaded page: 342
                        Source  Document Type  Subjects  Abstract  Lexile   \
0  Hindustan Times. 06/28/2018.        Article                               

  Ac

---news: 3520
---news: 3521
---news: 3522
---news: 3523
---news: 3524
---news: 3525
---news: 3526
---news: 3527
---news: 3528
---news: 3529
Downloaded page: 353
                                   Source  Document Type  Subjects  Abstract   \
0  Advertiser, The (Adelaide). 07/18/2007.                                      

  Lexile    Accession Number          Database   \
0          200707181037466706  Newspaper Source   

                                               title  \
0  Crude oil supplies not keeping up with global ...   

                                             content  
0   Source: Advertiser, The (Adelaide), JUL 18, 2...  
---news: 3530
---news: 3531
---news: 3532
---news: 3533
---news: 3534
---news: 3535
---news: 3536
---news: 3537
---news: 3538
---news: 3539
Downloaded page: 354
                                      Source  Document Type  Subjects   \
0  China Energy Newswire. 9/5/2011, p1-1. 1p.        Article             

                                        

---news: 3640
---news: 3641
---news: 3642
---news: 3643
---news: 3644
---news: 3645
---news: 3646
---news: 3647
---news: 3648
---news: 3649
Downloaded page: 365
                       Source  Document Type  Subjects   \
0  PR Newswire US. 10/06/2011.        Article             

                                           Abstract  Lexile   \
0  CALGARY, Alberta , Oct. 6, 2011 /PRNewswire/ -...           

                  Accession Number                Database   \
0  201110062037PR.NEWS.USPR.DA82467  Regional Business News   

                                          title  \
0  Canadian Crude Oil Trades on Argus WCS Index   

                                             content  
0  CALGARY, Alberta , Oct. 6, 2011 /PRNewswire/ -...  
---news: 3650
---news: 3651
---news: 3652
---news: 3653
---news: 3654
---news: 3655
---news: 3656
---news: 3657
---news: 3658
---news: 3659
Downloaded page: 366
                                Source  Document Type  Subjects   \
0  Business Wire (Engl

...

---news: 52465
---news: 52466
---news: 52467
---news: 52468
Downloaded page: 5792
                      Source  Document Type  Subjects   \
0  Oil& Gas News. 10/29/2014.                            

                                           Abstract  Lexile   \
0  (Dateline: HOUSTON: ) Marathon Petroleum Corpâ...           

                      Accession Number                Database   \
0  85d8ce590ad8981ca2c8286f79f599540149  Regional Business News   

                                    title  \
0  Marathonâ€™s CDU at Galveston restarts   

                                             content  
0  (Dateline: HOUSTON:  )Marathon Petroleum Corpâ...  
---news: 52469
---news: 52470
---news: 52471
---news: 52472
Downloaded page: 5793
                      Source  Document Type  Subjects   \
0  Oil& Gas News. 10/29/2014.                            

                                           Abstract  Lexile   \
0  (Dateline: HOUSTON: ) Marathon Petroleum Corpâ...           

        

---news: 52517
---news: 52518
---news: 52519
---news: 52520
Downloaded page: 5805
                      Source  Document Type  Subjects   \
0  Oil& Gas News. 10/29/2014.                            

                                           Abstract  Lexile   \
0  (Dateline: HOUSTON: ) Marathon Petroleum Corpâ...           

                      Accession Number                Database   \
0  85d8ce590ad8981ca2c8286f79f599540149  Regional Business News   

                                    title  \
0  Marathonâ€™s CDU at Galveston restarts   

                                             content  
0  (Dateline: HOUSTON:  )Marathon Petroleum Corpâ...  
---news: 52521
---news: 52522
---news: 52523
---news: 52524
Downloaded page: 5806
                      Source  Document Type  Subjects   \
0  Oil& Gas News. 10/29/2014.                            

                                           Abstract  Lexile   \
0  (Dateline: HOUSTON: ) Marathon Petroleum Corpâ...           

        

---news: 52569
---news: 52570
---news: 52571
---news: 52572
Downloaded page: 5818
                      Source  Document Type  Subjects   \
0  Oil& Gas News. 10/29/2014.                            

                                           Abstract  Lexile   \
0  (Dateline: HOUSTON: ) Marathon Petroleum Corpâ...           

                      Accession Number                Database   \
0  85d8ce590ad8981ca2c8286f79f599540149  Regional Business News   

                                    title  \
0  Marathonâ€™s CDU at Galveston restarts   

                                             content  
0  (Dateline: HOUSTON:  )Marathon Petroleum Corpâ...  
---news: 52573
---news: 52574
---news: 52575
---news: 52576
Downloaded page: 5819
                      Source  Document Type  Subjects   \
0  Oil& Gas News. 10/29/2014.                            

                                           Abstract  Lexile   \
0  (Dateline: HOUSTON: ) Marathon Petroleum Corpâ...           

        

---news: 52621
---news: 52622
---news: 52623
---news: 52624
Downloaded page: 5831
                      Source  Document Type  Subjects   \
0  Oil& Gas News. 10/29/2014.                            

                                           Abstract  Lexile   \
0  (Dateline: HOUSTON: ) Marathon Petroleum Corpâ...           

                      Accession Number                Database   \
0  85d8ce590ad8981ca2c8286f79f599540149  Regional Business News   

                                    title  \
0  Marathonâ€™s CDU at Galveston restarts   

                                             content  
0  (Dateline: HOUSTON:  )Marathon Petroleum Corpâ...  
---news: 52625
---news: 52626
---news: 52627
---news: 52628
Downloaded page: 5832
                      Source  Document Type  Subjects   \
0  Oil& Gas News. 10/29/2014.                            

                                           Abstract  Lexile   \
0  (Dateline: HOUSTON: ) Marathon Petroleum Corpâ...           

        

---news: 52673
---news: 52674
---news: 52675
---news: 52676
Downloaded page: 5844
                      Source  Document Type  Subjects   \
0  Oil& Gas News. 10/29/2014.                            

                                           Abstract  Lexile   \
0  (Dateline: HOUSTON: ) Marathon Petroleum Corpâ...           

                      Accession Number                Database   \
0  85d8ce590ad8981ca2c8286f79f599540149  Regional Business News   

                                    title  \
0  Marathonâ€™s CDU at Galveston restarts   

                                             content  
0  (Dateline: HOUSTON:  )Marathon Petroleum Corpâ...  
---news: 52677
---news: 52678
---news: 52679
---news: 52680
Downloaded page: 5845
                      Source  Document Type  Subjects   \
0  Oil& Gas News. 10/29/2014.                            

                                           Abstract  Lexile   \
0  (Dateline: HOUSTON: ) Marathon Petroleum Corpâ...           

        

In [106]:
page = list()
try:
    page[2]
except:
    print("wait")
    pass
print(page)

wait
[]


In [60]:
import json
data = {"3":2}
with open('data.json', 'a') as outfile:
    json.dump(data, outfile)

## 原本用 FULL SITE失敗的版本

In [1]:
url = "http://web.b.ebscohost.com/ehost/results?vid=3&sid=e7bbc51b-370f-47ca-a84b-4cee0644397e%40sessionmgr103&bquery=(crude+AND+oil)&bdata=JmRiPW5maCZkYj1id2gmY2xpMD1GVCZjbHYwPVkmdHlwZT0xJnNpdGU9ZWhvc3QtbGl2ZSZzY29wZT1zaXRl"
agents = {
    'accept': 'text/html,application/xhtml+xml,application/xml;q=0.9,image/webp,image/apng,*/*;q=0.8',
    'accept-Encoding': 'gzip, deflate',
    'accept-Language': 'zh-TW,zh;q=0.9,en-US;q=0.8,en;q=0.7,zh-CN;q=0.6',
    'cache-Control': 'max-age=0',
    'connection': 'keep-alive',
    'cookie': 'webauth=ug=7E36396631663D263E12395339&uc=1&un=e419d45f-3610-4919-8108-5ae3d1f24dd3&am=IP&pg=; VQPANKPS=025cef8b64-fab4-44Ds9EBfpGVK5C752Jx_JqeWZ7fLT-u4WXRGQ1xYADDrwsoQVESlHm0CKGvFahw5X5orw; BIGipServersdc-web-to-avi_80=593711882.20480.0000; __atuvc=9%7C43; EHost2=sid=a3a4fd39-3947-4105-aef7-4e23624f2a77@sessionmgr4007&k2=dGJyMPGstEqvq7dRrOPfgeyk44Dt6fIA&k3=dGJyMOPmtUq2qrBM&k4=ehost&k6=en&k7=live&k8=DS:live; amplitude_id_06d3064c4b7aa1187920f7d63c355898ebscohost.com=eyJkZXZpY2VJZCI6IjdjZDY5NjQxLTBmMGUtNDM2MC05MGJlLWNmNjIyNDA4YmViZVIiLCJ1c2VySWQiOm51bGwsIm9wdE91dCI6ZmFsc2UsInNlc3Npb25JZCI6MTU0MDIyMDc1NTQ3OCwibGFzdEV2ZW50VGltZSI6MTU0MDIyMDc3NTkyNiwiZXZlbnRJZCI6MzQsImlkZW50aWZ5SWQiOjM0LCJzZXF1ZW5jZU51bWJlciI6Njh9',
    'host': 'web.b.ebscohost.com',
    'upgrade-Insecure-Requests': '1',
    'user-Agent': 'Mozilla/5.0 (Windows NT 10.0) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/65.0.3325.181 Safari/537.36'
}

def news_crawler(url,agents,sub_start,sub_end):
    request = urllib.request.Request(url, headers=agents)
    html = urllib.request.urlopen(request, timeout=5).read()
    encoding = (urllib.request.urlopen(request, timeout=5)).getheader('Content-Encoding')
    #    print(encoding)
    html = gzip.decompress(html).decode("utf-8")
    html = html[html.find(sub_start):html.find(sub_end)]
    soup = BeautifulSoup(html, "html5lib")
    return(soup)

def extract_abstract(soup):
    abstracts = list()
    infos = soup.findAll("div",{"class":"display-info"})
    for info in infos:
        info = info.get_text()
        if info.find("Abstract") ==-1:
            abstracts.append(" ")
        else:
            start = info.find("Abstract")
            if info.find("Reading Level")!=-1:
                end = info.find("Reading Level")
            elif info.find("Database")!=-1:
                end = info.find("Database")
            else:
                end = -1
            abstracts.append(info[start:end])
    return(abstracts)

In [131]:
sub_start = "<a class=\"title-link color-p4\" name="
sub_end = "content-footer"
soup = news_crawler(url,agents,sub_start,sub_end)

In [132]:
titles = list()
urls = list()
source_dates = list()
abstracts = list()
content = list()

news_list = soup.findAll("a", {"class": "title-link color-p4"})

for news in news_list:
    titles.append(news['title'])
    urls.append(news['href'])

abstracts = abstracts + extract_abstract(soup)

sub_start = "<a name=\"citation\" data-auto=\"citation_title\">"
sub_end = "<hr noshade=\"noshade\">"
count = 1
for url in urls:
    print("Downloading article:",count)
    count = count + 1
    article = str()
    news_soup = news_crawler(url,agents,sub_start,sub_end)
    features = news_soup.findAll("dd")
    source_dates.append(features[0].get_text())
#     doc_types.append(features[1].get_text())
#     abstracts.append(features[2].get_text())
    body = news_soup.findAll("p",{"class":"body-paragraph"})
    for p in body:
        article = article+p.get_text()
    content.append(article)
    

In [133]:
import pandas as pd
pd.DataFrame({"titles":titles,"urls":urls,"source":source_dates,"abstracts":abstracts,"content":content})

titles  \
0   Energy Transfer, Magellan Midstream, MPLX and ...   
1   Matrix Service Inc. Awarded Full EPC by Large ...   
2   IEA: Crude Will Top $80 If Oil Production Drop...   
3     EPIC Pipeline To Switch To Carrying Crude Oil.    
4   Oil Prices Rally As U.S. Inventories, Iranian ...   
5   CME Group Inc to Launch Physical WTI Houston C...   
6   Tallgrass Energy and Silver Creek Midstream Ag...   
7   EPIC Announces Plans to Begin Interim Crude Oi...   
8   Medallion Pipeline Announces Successful Open S...   
9   Crude Oil Prices Could Increase As U.S. Leaves...   
10  Enterprise Conducts Open Season for West Texas...   
11  Kingfisher Midstream, Blueknight Energy Partne...   
12  2018 Advances in Oil & Gas Encapsulation, Pipe...   
13  Crude Oil Carriers: Global Market Opportunitie...   
14  Crude Oil Desalter - Global Market Forecast to...   
15  Oryx Midstream Services II, LLC Further Extend...   
16  Oryx Midstream Services II, LLC Extends Bindin...   
17  JupiterMLP Receives Funding To Advance Constru...   
18  Emerging Opportunities for Materials Derived f...   
19  Oil Storage Market is Anticipated To Witness S...   
20  Salt Creek Midstream to Partner with Noble Mid...   
21  Crude Oil Carriers: Global Market Opportunitie...   
22  Energy Transfer, Magellan Midstream, MPLX and ...   
23  Crude Oil Desalter - Global Market Forecast to...   
24  Global Crude Oil Desalter Market 2018-2022 | I...   
25  Tallgrass to Develop New Cushing to St. James ...   
26  Global Crude Oil Carriers Market Outlook 2017-...   
27  3 Day Conference: Plastics beyond Petroleum: B...   
28  Crude Oil-to-Chemicals and Other Disruptive Te...   
29  EPIC Secures Strategic Partnerships for Permia...   
30  Global Crude Oil Carriers Market Outlook 2017-...   
31  Phillips 66 Partners to Construct West Texas C...   
32      Advisory Vote 19 involves a tax on crude oil    
33  Global Crude Oil Flow Improvers (COFI) Market ...   
34           SCG predicts crude oil to hit $74 in Q4    
35  Flinders University Scientists Develop New Env...   
36  BRIEF: Shippers warn rising crude oil price wi...   
37  Global Crude Oil Flow Improvers Market - Shift...   
38  Global Crude Oil Market 2018 with ExxonMobil, ...   
39  Global Shale Oil Market 2018-2022: Uncertainti...   
40  Crude Tops $75, And These 5 Oil Stocks Are Mov...   
41  Rocky Mountain Crude Oil Announces Acquisition...   
42  N.D. Senate candidates feud over who gets cred...   
43  Kyzylorda region's oil fields may export more ...   
44  Kyzylorda region's oil fields may export more ...   
45               OTTCO â€“ Ras Markaz Crude Oil Park    
46  Global Crude Oil Flow Improvers (COFI) Market ...   
47  EPIC Crude Oil Pipeline Announces Successful C...   
48  Global Crude Oil Market 2018 with ExxonMobil, ...   
49  Global Crude Oil and Natural Gas Market Briefi...   

                                                 urls  \
0   http://web.b.ebscohost.com/ehost/viewarticle/r...   
1   http://web.b.ebscohost.com/ehost/viewarticle/r...   
2   http://web.b.ebscohost.com/ehost/viewarticle/r...   
3   http://web.b.ebscohost.com/ehost/viewarticle/r...   
4   http://web.b.ebscohost.com/ehost/viewarticle/r...   
5   http://web.b.ebscohost.com/ehost/viewarticle/r...   
6   http://web.b.ebscohost.com/ehost/viewarticle/r...   
7   http://web.b.ebscohost.com/ehost/viewarticle/r...   
8   http://web.b.ebscohost.com/ehost/viewarticle/r...   
9   http://web.b.ebscohost.com/ehost/viewarticle/r...   
10  http://web.b.ebscohost.com/ehost/viewarticle/r...   
11  http://web.b.ebscohost.com/ehost/viewarticle/r...   
12  http://web.b.ebscohost.com/ehost/viewarticle/r...   
13  http://web.b.ebscohost.com/ehost/viewarticle/r...   
14  http://web.b.ebscohost.com/ehost/viewarticle/r...   
15  http://web.b.ebscohost.com/ehost/viewarticle/r...   
16  http://web.b.ebscohost.com/ehost/viewarticle/r...   
17  http://web.b.ebscohost.com/ehost/viewarticle/r...   
18  http://web.b.ebscohost.com/ehost/viewarticle/r...   

In [5]:
import requests

In [37]:
url = "http://web.a.ebscohost.com/ehost/results?vid=2&sid=3c6f333f-0bd1-4253-a615-5e5989af2118%40sdc-v-sessmgr01&bquery=(crude+AND+oil)&bdata=JmRiPW5maCZkYj1id2gmY2xpMD1GVCZjbHYwPVkmdHlwZT0xJnNpdGU9ZWhvc3QtbGl2ZSZzY29wZT1zaXRl"
header = {
    "Accept": "text/html,application/xhtml+xml,application/xml;q=0.9,image/webp,image/apng,*/*;q=0.8",
    "Accept-Encoding": "gzip, deflate",
    "Accept-Language": "zh-TW,zh;q=0.9,en-US;q=0.8,en;q=0.7",
    "Connection": "keep-alive",
    "Cookie": "webauth=ug=7E36396631663D263E12395339&uc=1&un=e419d45f-3610-4919-8108-5ae3d1f24dd3&am=IP&pg=; VQPANKPS=025cef8b64-fab4-44Ds9EBfpGVK5C752Jx_JqeWZ7fLT-u4WXRGQ1xYADDrwsoQVESlHm0CKGvFahw5X5orw; BIGipServersdc-web-to-avi_80=593711882.20480.0000; EHost2=sid=a3a4fd39-3947-4105-aef7-4e23624f2a77@sessionmgr4007&k2=dGJyMPGstEqvq7dRrOPfgeyk44Dt6fIA&k3=dGJyMOPmtUq2qrBM&k4=ehost&k6=en&k7=live&k8=DS:live; ReadSpeakerSettings=rsLang=en_us; amplitude_id_06d3064c4b7aa1187920f7d63c355898ebscohost.com=eyJkZXZpY2VJZCI6IjdjZDY5NjQxLTBmMGUtNDM2MC05MGJlLWNmNjIyNDA4YmViZVIiLCJ1c2VySWQiOm51bGwsIm9wdE91dCI6ZmFsc2UsInNlc3Npb25JZCI6MTU0MDI5NDMyOTg2MCwibGFzdEV2ZW50VGltZSI6MTU0MDI5NjQxMjk1NywiZXZlbnRJZCI6MTI4LCJpZGVudGlmeUlkIjoxMTcsInNlcXVlbmNlTnVtYmVyIjoyNDV9; __atuvc=36%7C43",
    "Host": "web.a.ebscohost.com",
    "Referer": "http://web.a.ebscohost.com/plink?key=10.83.8.65_8000_1172840722&bquery=(crude+AND+oil)&db=nfh&db=bwh&cli0=FT&clv0=Y&type=1&site=ehost-live&scope=site",
    "Upgrade-Insecure-Requests": 1,
    "User-Agent": "Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/70.0.3538.67 Safari/537.36",
}
data = {
    "RelRequestPath": "resultsadvanced",
    "__EVENTTARGET": "ctl00$ctl00$MainContentArea$MainContentArea$bottomMultiPage$rptPageLinks$ctl02$lnkPageLink",
    "__EVENTARGUMENT": ""
}
r = requests.post(url,data=data,headers = agents)

In [38]:
sub_start = "<a class=\"title-link color-p4\" name="
sub_end = "content-footer"
html = str(r.content)
html = html[html.find(sub_start):html.find(sub_end)]
soup = BeautifulSoup(html, "html5lib")
soup.prettify

<bound method Tag.prettify of <html><head></head><body><a accesskey="1" class="title-link color-p4" href="http://web.b.ebscohost.com/ehost/viewarticle/render?data=dGJyMPPp44rp2%2fdV0%2bnjisfk5Ie46bROsKezUbek63nn5Kx95uXxjL6nrkewqa1Krqe2OLawski4q7Q4v8OkjPDX7Ivf2fKB7eTnfLujtU%2b1p69Nrqa0PurX7H%2b72%2bw%2b4ti7evXepIzf3btZzJzfhrunsUm0qbdIsaqkfu3o63nys%2bSN6uLyffbq&amp;vid=2&amp;sid=3c6f333f-0bd1-4253-a615-5e5989af2118@sdc-v-sessmgr01" id="Result_1" name="Result_1" onclick="__doLinkPostBack(\'\',\'target~~fulltext||args~~1\',\'\');return false;" title="Energy Transfer, Magellan Midstream, MPLX and Delek to Jointly Construct the Permian Gulf Coast or PGC Pipeline for Permian Basin Crude Oil Takeaway. ">Energy Transfer, Magellan Midstream, MPLX and Delek to Jointly Construct the Permian Gulf Coast or PGC Pipeline for Permian Basin <strong>Crude</strong> <strong>Oil</strong> Takeaway. </a><em class="preview-hover fulltext-hover no-img-hover" data-hoverpreviewjson='{"db":"bwh","tag":"AN","term":

In [ ]:
import re

from scrapy.http import FormRequest
from scrapy.spider import BaseSpider


HEADERS = {
    'X-MicrosoftAjax': 'Delta=true',
    'User-Agent': 'Mozilla/5.0 (Macintosh; Intel Mac OS X 10_10_2) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/41.0.2272.76 Safari/537.36'
}
URL = 'http://exitrealty.com/agent_list.aspx?firstName=&lastName=&country=USA&state=NY'


class ExitRealtySpider(BaseSpider):
    name = "exit_realty"

    allowed_domains = ["exitrealty.com"]
    start_urls = [URL]

    def parse(self, response):
        # submit a form (first page)
        self.data = {}
        for form_input in response.css('form#aspnetForm input'):
            name = form_input.xpath('@name').extract()[0]
            try:
                value = form_input.xpath('@value').extract()[0]
            except IndexError:
                value = ""
            self.data[name] = value

        self.data['ctl00$MainContent$ScriptManager1'] = 'ctl00$MainContent$UpdatePanel1|ctl00$MainContent$agentList'
        self.data['__EVENTTARGET'] = 'ctl00$MainContent$List'
        self.data['__EVENTARGUMENT'] = 'Page$1'

        return FormRequest(url=URL,
                           method='POST',
                           callback=self.parse_page,
                           formdata=self.data,
                           meta={'page': 1},
                           dont_filter=True,
                           headers=HEADERS)

    def parse_page(self, response):
        current_page = response.meta['page'] + 1

        # parse agents (TODO: yield items instead of printing)
        for agent in response.xpath('//a[@class="regtext"]/text()'):
            print agent.extract()
        print "------"

        # request the next page
        data = {
            '__EVENTARGUMENT': 'Page$%d' % current_page,
            '__EVENTVALIDATION': re.search(r"__EVENTVALIDATION\|(.*?)\|", response.body, re.MULTILINE).group(1),
            '__VIEWSTATE': re.search(r"__VIEWSTATE\|(.*?)\|", response.body, re.MULTILINE).group(1),
            '__ASYNCPOST': 'true',
            '__EVENTTARGET': 'ctl00$MainContent$agentList',
            'ctl00$MainContent$ScriptManager1': 'ctl00$MainContent$UpdatePanel1|ctl00$MainContent$agentList',
            '': ''
        }

        return FormRequest(url=URL,
                           method='POST',
                           formdata=data,
                           callback=self.parse_page,
                           meta={'page': current_page},
                           dont_filter=True,
                           headers=HEADERS)